In [1]:
import kerchunk
import xarray as xr
from kerchunk.hdf import SingleHdf5ToZarr
from kerchunk.combine import MultiZarrToZarr
import fsspec
from glob import glob
import xradar as xd
import matplotlib.pyplot as plt
import cmweather
import numpy as np
import hvplot.xarray
import cartopy.crs as ccrs
import pyproj
from wradlib.georef import epsg_to_osr, georeference
from xarray.core.datatree import DataTree
from zarr.errors import ContainsGroupError  

In [2]:
def fix_angle(ds: xr.Dataset, exp_dim="volume_time", tolerance=1.0, **kwargs) -> xr.Dataset:
    """
    This function reindex the radar azimuth angle to make all sweeps starts and end at the same angle
    @param ds: xarray dataset containing and xradar object
    @return: azimuth reindex xarray dataset
    """
    ds["time"] = ds.time.load() 
    angle_dict = xd.util.extract_angle_parameters(ds)
    start_ang = angle_dict["start_angle"]
    stop_ang = angle_dict["stop_angle"]
    direction = angle_dict["direction"]
    ds = xd.util.remove_duplicate_rays(ds)
    az = len(np.arange(start_ang, stop_ang))
    ar = np.round(az / len(ds.azimuth.data), 2)
    ds = xd.util.reindex_angle(
        ds, start_ang, stop_ang, ar, direction, method="nearest", tolerance=tolerance, **kwargs
    )
        
    ds = ds.expand_dims(exp_dim)  # Expand for volumes for concatenation
    ds[exp_dim] = [np.nanmin(ds.time.values)]
    
    return ds

In [3]:
radars = {
    "cband": "/media/alfonso/drive/Laura/ERAD/20240522_MeteoSwiss_ARPA_Lombardia/Data/Cband/MonteLema", 
    "xband": "/media/alfonso/drive/Laura/ERAD/20240522_MeteoSwiss_ARPA_Lombardia/Data/Xband/DES_VOL_RAW",
         }

In [ ]:
for key in list(radars.keys()):
    print(key)
    erad_files = sorted(glob(f"{radars[key]}*.nc"))
    dt = xd.io.open_cfradial1_datatree(erad_files[0])
    groups = [
        i[1:] for i in list(dt.groups) if i.startswith("/sweep") if i not in ["/"]
    ]
    for group in groups:
        root = {}
        ds = xr.open_mfdataset(
            erad_files,
            preprocess=fix_angle,
            engine="cfradial1",
            group=group,
            concat_dim="volume_time",
            combine="nested",
        ).xradar.georeference()
        root[f"{key}/{group}"] = ds
        dtree = DataTree.from_dict(root)
        try:
            dtree.to_zarr("/media/alfonso/drive/Alfonso/python/zarr_radar/erad_2024.zarr", consolidated=True)
        except ContainsGroupError:
            dtree.to_zarr("/media/alfonso/drive/Alfonso/python/zarr_radar/erad_2024.zarr", consolidated=True, mode="a")
    
        del dtree, ds

In [4]:
# dtree = xr.backends.api.open_datatree("/media/alfonso/drive/Alfonso/python/zarr_radar/erad_2024.zarr", engine="zarr", consolidated=True, chunks={})

In [7]:
dtree

DataTree('None', parent=None)
├── DataTree('cband')
│   ├── DataTree('sweep_0')
│   │       Dimensions:                              (azimuth: 360, volume_time: 73,
│   │                                                 range: 492)
│   │       Coordinates:
│   │           altitude                             float32 4B ...
│   │         * azimuth                              (azimuth) float32 1kB 0.5 1.5 ... 359.5
│   │           crs_wkt                              int64 8B ...
│   │           elevation                            (volume_time, azimuth) float32 105kB dask.array<chunksize=(73, 360), meta=np.ndarray>
│   │           latitude                             float32 4B ...
│   │           longitude                            float32 4B ...
│   │         * range                                (range) float32 2kB 250.0 ... 2.457e+05
│   │           time                                 (volume_time, azimuth) datetime64[ns] 210kB dask.array<chunksize=(73, 360), meta=np.ndarray>
│   │         * volume_time                          (volume_time) datetime64[ns] 584B 20...
│   │           x                                    (azimuth, range, volume_time) float64 103MB dask.array<chunksize=(45, 123, 19), meta=np.ndarray>
│   │           y                                    (azimuth, range, volume_time) float64 103MB dask.array<chunksize=(45, 123, 19), meta=np.ndarray>
│   │           z                                    (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(10, 90, 123), meta=np.ndarray>
│   │       Data variables: (12/14)
│   │           differential_reflectivity            (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           nyquist_velocity                     (volume_time, azimuth) float32 105kB dask.array<chunksize=(1, 360), meta=np.ndarray>
│   │           pulse_width                          (volume_time, azimuth) timedelta64[ns] 210kB dask.array<chunksize=(1, 360), meta=np.ndarray>
│   │           reflectivity                         (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           reflectivity_hh_clut                 (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           reflectivity_vv                      (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           ...                                   ...
│   │           sweep_fixed_angle                    (volume_time) float32 292B dask.array<chunksize=(73,), meta=np.ndarray>
│   │           sweep_mode                           (volume_time) <U20 6kB dask.array<chunksize=(73,), meta=np.ndarray>
│   │           sweep_number                         (volume_time) int64 584B dask.array<chunksize=(73,), meta=np.ndarray>
│   │           uncorrected_cross_correlation_ratio  (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           uncorrected_differential_phase       (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   │           velocity                             (volume_time, azimuth, range) float64 103MB dask.array<chunksize=(1, 360, 492), meta=np.ndarray>
│   ├── DataTree('sweep_1')
│   │       Dimensions:                              (azimuth: 360, volume_time: 73,
│   │                                                 range: 492)
│   │       Coordinates:
│   │           altitude                             float32 4B ...
│   │         * azimuth                              (azimuth) float32 1kB 0.5 1.5 ... 359.5
│   │           crs_wkt                              int64 8B ...
│   │           elevation                            (volume_time, azimuth) float32 105kB dask.array<chunksize=(73, 360), meta=np.ndarray>
│   │           latitude                             float32 4B ...
│   │           longitude

In [5]:
# Set the URL and path for the cloud
URL = 'https://js2.jetstream-cloud.org:8001/'
path = f'pythia/radar/erad2024'

fs = fsspec.filesystem("s3", anon=True, client_kwargs=dict(endpoint_url=URL))

fs.glob(f"{path}/*")

['pythia/radar/erad2024/20240522_MeteoSwiss_ARPA_Lombardia',
 'pythia/radar/erad2024/dda_data']

In [6]:
mapper = fs.get_mapper(f"{path}/erad_2024.zarr")

In [7]:
%%time
dtree.to_zarr(mapper, consolidated=True, mode="w")

KeyError: '.zgroup'